In [70]:
import pickle
import torch
import transformers
from transformers import AutoTokenizer, AutoModel, AutoConfig
from transformers import BertTokenizer, BertModel
from torch.utils.data import Dataset, DataLoader

import torch.nn.functional as F
import numpy as np

import math
import pandas as pd
import pip
import re

import time

import random

import re




random.seed(123)

torch.manual_seed(123)
from sklearn.metrics import jaccard_score, f1_score, accuracy_score, recall_score, precision_score, confusion_matrix

torch.cuda.manual_seed_all(123)
np.random.seed(123)

In [2]:
from transformers.models.bert.modeling_bert import BertPreTrainedModel, BertModel, BertConfig

In [3]:
# from model import JointBERT, JointDistilBERT, JointAlbert

In [4]:
with open("final_dialog_sheet1", "rb") as f:
    final_dialog_sheet1 = pickle.load(f)

In [5]:
final_dialog_sheet1

[{'dialogue_id': 1059,
  'correct_disease_tag': 'central retinal artery or vein occlusion',
  'disease_tag': 'central retinal artery or vein occlusion',
  'masked_dialog': ["Patient : Doctor, I see Spots or clouds in my vision. I can't see anything clearly. I feel helpless.",
   'Doctor : I understand how you feel. I need to ask a few questions to diagnose your disease. Have you got [MASK]?',
   'Patient : True, I am also dealing with Diminished vision.',
   'Doctor : Do you have [MASK]?',
   'Patient : Yes, I have got Symptoms of eye.',
   'Doctor : Have you felt [MASK]?',
   'Patient : Indeed, I am suffering from Pain in eye.',
   'Doctor : Your symptoms indicate that you have [MASK].'],
  'symptom_dialog_extracted': ['Diminished vision',
   'Symptoms of eye',
   'Pain in eye']},
 {'dialogue_id': 19510,
  'correct_disease_tag': 'degenerative disc disease',
  'disease_tag': 'degenerative disc disease',
  'masked_dialog': ['Patient : Doctor, I have Shoulder pain. I feel terrible. Would

In [6]:
len(final_dialog_sheet1)

893

In [7]:
with open("final_dialog_sheet2", "rb") as f:
    final_dialog_sheet2 = pickle.load(f)

In [8]:
final_dialog_sheet2

[{'dialogue_id': 27157,
  'correct_disease_tag': 'fracture of the pelvis',
  'disease_tag': 'fracture of the pelvis',
  'masked_dialog': ['Patient : Doctor, I am suffering from Hip pain. It is making me difficult to sit. Help me.',
   "Doctor : I will help you, I am sorry to hear you can't sit properly. Ok, are you suffering from [MASK]?",
   'Patient : Yes Doctor.',
   'Doctor : You might have [MASK].'],
  'symptom_dialog_extracted': ['Groin pain']},
 {'dialogue_id': 6872,
  'correct_disease_tag': 'conversion disorder',
  'disease_tag': 'conversion disorder',
  'masked_dialog': ['Patient : Doctor, I am feeling Seizures. I am unable to control movements of my arms and legs. Please help me.',
   'Doctor : That can be disturbing and I will try to fix it.  Can you tell me are you dealing with [MASK]?',
   'Patient : I think I am in depression. I am felling restlessness. Help me out.',
   "Doctor : Sure I'll. It ishard to be in such situation. Can you begin by saying, is there any [MASK] i

In [9]:
all_dialog = final_dialog_sheet1 + final_dialog_sheet2

In [10]:
all_dialog

[{'dialogue_id': 1059,
  'correct_disease_tag': 'central retinal artery or vein occlusion',
  'disease_tag': 'central retinal artery or vein occlusion',
  'masked_dialog': ["Patient : Doctor, I see Spots or clouds in my vision. I can't see anything clearly. I feel helpless.",
   'Doctor : I understand how you feel. I need to ask a few questions to diagnose your disease. Have you got [MASK]?',
   'Patient : True, I am also dealing with Diminished vision.',
   'Doctor : Do you have [MASK]?',
   'Patient : Yes, I have got Symptoms of eye.',
   'Doctor : Have you felt [MASK]?',
   'Patient : Indeed, I am suffering from Pain in eye.',
   'Doctor : Your symptoms indicate that you have [MASK].'],
  'symptom_dialog_extracted': ['Diminished vision',
   'Symptoms of eye',
   'Pain in eye']},
 {'dialogue_id': 19510,
  'correct_disease_tag': 'degenerative disc disease',
  'disease_tag': 'degenerative disc disease',
  'masked_dialog': ['Patient : Doctor, I have Shoulder pain. I feel terrible. Would

In [11]:
len(all_dialog)

1396

In [12]:
dlog_sheet = []
label_sheet = []
dlog_id_sheet = []

counter = 1
total_dialogues_generated = 0
for dg in all_dialog:
    print('Dialog number : ',counter)
    counter += 1
    print('dialogue_id : ', dg['dialogue_id'])
    dlog = dg['masked_dialog']
#     print(dlog)
#     dlog = final_dialog_with_masked_symptom[1]['masked_dialog']
    extracted = dg['symptom_dialog_extracted']
    disease7 = dg['correct_disease_tag']

#     print('Total number of sub dialogues generated will be : ', len(dlog)//2)
    sub_dialog_counter = 1
    for i in range(0,len(dlog),2):
#         print("Sub dialog number : ", sub_dialog_counter)
        sub_dialog_counter += 1
        total_dialogues_generated += 1
#         print('Ith count : ',i)
        temp_list = []
        temp_list = list(dlog[:i+2])
#         print(temp_list)

        z = (len(dlog)-2)
        to_predict = ''
        if(i == z):
#             print('////////')
#             print('Its disease prediction time')
            cnt = 0
            for j in range(len(temp_list)-1):
                if(j%2!=0):
#                     print('Extracted : ', extracted[cnt])
#                     print(temp_list[j])
                    temp_list[j] = temp_list[j].replace('[MASK]',extracted[cnt])
    #                 print(temp_list[j])
                    cnt += 1
            to_predict = disease7
            print(temp_list)
            
            label_dlog = to_predict.lower()
            print(label_dlog)
            # if ( label_dlog == 'Diaper rash' or label_dlog == 'diaper rash'):
            #     continue
            dlog_sheet.append(temp_list)
            label_sheet.append(label_dlog)
            dlog_id_sheet.append(dg['dialogue_id'])
            print()
        else:
            cnt = 0
            for j in range(len(temp_list)-1):
                if(j%2!=0):
#                     print('Extracted : ', extracted[cnt])
#                     print(temp_list[j])
                    temp_list[j] = temp_list[j].replace('[MASK]',extracted[cnt])
    #                 print(temp_list[j])
                    cnt += 1

            to_predict = extracted[cnt]

        
        
        

#         print()
    print()

Dialog number :  1
dialogue_id :  1059
["Patient : Doctor, I see Spots or clouds in my vision. I can't see anything clearly. I feel helpless.", 'Doctor : I understand how you feel. I need to ask a few questions to diagnose your disease. Have you got Diminished vision?', 'Patient : True, I am also dealing with Diminished vision.', 'Doctor : Do you have Symptoms of eye?', 'Patient : Yes, I have got Symptoms of eye.', 'Doctor : Have you felt Pain in eye?', 'Patient : Indeed, I am suffering from Pain in eye.', 'Doctor : Your symptoms indicate that you have [MASK].']
central retinal artery or vein occlusion


Dialog number :  2
dialogue_id :  19510
['Patient : Doctor, I have Shoulder pain. I feel terrible. Would you please tell me what could be its cause?', 'Doctor :  I can feel the pain you feel. Let me ask you some questions. Do you have Back pain?', 'Patient : Literally, I am suffering from Back pain.', 'Doctor : Do you have Low back pain?', 'Patient : Yes, I am dealing with Low back pai

dialogue_id :  24939
['Patient : Hi Doctor, why am I having Skin lesion. I have problem in skin, please help.', 'Doctor : I realize your condition, I will try to diagnose it. Based on your symptoms you have [MASK].']
decubitus ulcer


Dialog number :  346
dialogue_id :  23730
['Patient : Please check my skin Skin rash', 'Doctor : Let me check, do you have Itching of skin?', 'Patient : True sometimes I have Itching of skin.', 'Doctor : Based on your symptoms you have [MASK].']
contact dermatitis


Dialog number :  347
dialogue_id :  7247
["Patient : Doctor, I am facing Nausea. I feel uncomfortable in stomach, what's wrong with me?", "Doctor : I understand your concern that feeling uncomfortable in stomach can make one feel restless in one's mind. That sounds frustrating, are you having Headache?", 'Patient : Yes doctor.', 'Doctor : Based on your symptoms you have [MASK].']
carbon monoxide poisoning


Dialog number :  348
dialogue_id :  14058
["Patient : Hi Doctor, why am I having Low ba

dialogue_id :  18365
['Patient : Hello doctor, I see spots or clouds in vision. I cannot see clearly. Please help.', 'Doctor : Okay, I understand your concern. But tell me if you do have Lacrimation?', 'Patient : I think so.', 'Doctor : Have you felt Pain in eye?', 'Patient : Exactly, I do feel Pain in eye. It is getting worse.', 'Doctor : I can understand your pain. Are you struggling with Abnormal movement of eyelid?', 'Patient : Yes, I am struggling with it.', 'Doctor : Do you have Symptoms of eye?', 'Patient : True, I have got Symptoms of eye.', 'Doctor : Are you suffering from Eye redness?', 'Patient : I am not sure, please have a look, Eye redness.', 'Doctor : Have you got Diminished vision?', 'Patient : Right, I have got Diminished vision.', 'Doctor : You may have [MASK].']
ectropion


Dialog number :  703
dialogue_id :  3105
['Patient : Good morning doctor, I am suffering from Dizziness. I have to get better before my trip.', 'Doctor : This is very much likely to happen if you 

dialogue_id :  16141
['Patient : Hello doctor,I have problem with Sweating. It is causing shirt and trousers get soaked with sweat.', 'Doctor : I understand what you are saying. You might have [MASK]']
graves disease


Dialog number :  1060
dialogue_id :  16664
['Patient : Doctor, take a look at Skin rash and tell me if there is something wrong?', 'Doctor : Have you got Fever?', 'Patient : Yes doctor.', 'Doctor : Do you ever notice Abnormal appearing skin?', 'Patient : Yes.', 'Doctor : Are you dealing with a Ache all over?', 'Patient : Yes doctor.', 'Doctor : Are you dealing with Cough?', 'Patient : Yes doctor, I am dealing with Cough.', 'Doctor : Do you have any Problems during pregnancy?', 'Patient : Yes.', 'Doctor : You may have [MASK]']
chickenpox


Dialog number :  1061
dialogue_id :  26294
['Patient : Hello doctor, I am dealing with Diminished vision. It is taking away colours of my life.', 'Doctor : You are making total sense. You might have [MASK]']
diabetic retinopathy


Dialo

In [13]:
dlog_sheet

[["Patient : Doctor, I see Spots or clouds in my vision. I can't see anything clearly. I feel helpless.",
  'Doctor : I understand how you feel. I need to ask a few questions to diagnose your disease. Have you got Diminished vision?',
  'Patient : True, I am also dealing with Diminished vision.',
  'Doctor : Do you have Symptoms of eye?',
  'Patient : Yes, I have got Symptoms of eye.',
  'Doctor : Have you felt Pain in eye?',
  'Patient : Indeed, I am suffering from Pain in eye.',
  'Doctor : Your symptoms indicate that you have [MASK].'],
 ['Patient : Doctor, I have Shoulder pain. I feel terrible. Would you please tell me what could be its cause?',
  'Doctor :  I can feel the pain you feel. Let me ask you some questions. Do you have Back pain?',
  'Patient : Literally, I am suffering from Back pain.',
  'Doctor : Do you have Low back pain?',
  'Patient : Yes, I am dealing with Low back pain.',
  'Doctor : Are you also dealing with Neck pain?',
  'Patient : True, I have got Neck pain.'

In [14]:
len(dlog_sheet)

1396

In [15]:
label_sheet

['central retinal artery or vein occlusion',
 'degenerative disc disease',
 'diabetic retinopathy',
 'chronic back pain',
 'air embolism',
 'dyshidrosis',
 'conversion disorder',
 'anxiety',
 'conductive hearing loss',
 'alcohol intoxication',
 'conductive hearing loss',
 'drug reaction',
 'air embolism',
 'granuloma inguinale',
 'extrapyramidal effect of drugs',
 'corneal disorder',
 'encephalitis',
 'eczema',
 'extrapyramidal effect of drugs',
 'actinic keratosis',
 'endometrial cancer',
 'adjustment reaction',
 'drug abuse cocaine',
 'chondromalacia of the patella',
 'chalazion',
 'central retinal artery or vein occlusion',
 'alzheimer disease',
 'endometriosis',
 'acariasis',
 'epidural hemorrhage',
 'guillain barre syndrome',
 'acute kidney injury',
 'cerebral edema',
 'corneal disorder',
 'drug reaction',
 'cushing syndrome',
 'contact dermatitis',
 'eczema',
 'epididymitis',
 'chickenpox',
 'flat feet',
 'dissociative disorder',
 'chickenpox',
 'chondromalacia of the patella',
 

In [16]:
len(label_sheet)

1396

In [17]:
dlog_id_sheet

[1059,
 19510,
 25630,
 1467,
 5780,
 26258,
 22733,
 1564,
 29211,
 26235,
 16427,
 16512,
 17308,
 16360,
 15081,
 15386,
 18363,
 27441,
 9641,
 27768,
 21778,
 18706,
 7857,
 29589,
 15191,
 22535,
 6047,
 20116,
 26439,
 11928,
 20634,
 3590,
 3726,
 7899,
 9125,
 27079,
 7995,
 21990,
 12775,
 86,
 19263,
 19699,
 19386,
 23606,
 14328,
 14382,
 27516,
 17279,
 20111,
 19480,
 28758,
 7769,
 5013,
 26904,
 19940,
 3996,
 12006,
 6762,
 2874,
 9180,
 18054,
 12207,
 17117,
 20286,
 13025,
 791,
 10394,
 23176,
 26863,
 11005,
 9671,
 11134,
 15276,
 16094,
 6624,
 6097,
 16311,
 339,
 16364,
 19563,
 4346,
 27942,
 7828,
 13246,
 16560,
 19534,
 120,
 8868,
 1947,
 28436,
 5509,
 24423,
 14480,
 13768,
 22417,
 21493,
 23450,
 23404,
 22550,
 20582,
 11716,
 18034,
 5402,
 4711,
 20581,
 7456,
 750,
 29975,
 28051,
 15254,
 25468,
 26528,
 275,
 10852,
 6183,
 23318,
 29262,
 14475,
 28630,
 621,
 18230,
 19696,
 15869,
 18797,
 880,
 17314,
 11154,
 10795,
 6953,
 29134,
 11948,


In [18]:
len(dlog_id_sheet)

1396

In [19]:
dlog_sheet[946]

['Patient : Doctor, My baby got Fever. Baby is suffering because of it help us.',
 'Doctor : I can feel the pain you feel. Does He or She suffering from Diarrhea?',
 'Patient : Yes Doctor.',
 'Doctor : Your child may have [MASK].']

In [20]:
all_dialog[946]

{'dialogue_id': 20443,
 'correct_disease_tag': 'diaper rash',
 'disease_tag': 'diaper rash',
 'masked_dialog': ['Patient : Doctor, My baby got Fever. Baby is suffering because of it help us.',
  'Doctor : I can feel the pain you feel. Does He or She suffering from [MASK]?',
  'Patient : Yes Doctor.',
  'Doctor : Your child may have [MASK].'],
 'symptom_dialog_extracted': ['Diarrhea']}

In [21]:
dlog_id_sheet[946]

20443

In [22]:
label_sheet[946]

'diaper rash'

In [23]:
all_dialog_file = []

for i in range(len(dlog_sheet)):
    temp_dict = {}
    temp_dlog_id_sheet = dlog_id_sheet[i]
    temp_dlog_sheet = dlog_sheet[i]
    temp_label_sheet = label_sheet[i]
    
    temp_dict['dialog_id'] = temp_dlog_id_sheet
    temp_dict['masked_dialog'] = temp_dlog_sheet
    temp_dict['disease_tag'] = temp_label_sheet
    
    all_dialog_file.append(temp_dict)
    

In [24]:
all_dialog_file

[{'dialog_id': 1059,
  'masked_dialog': ["Patient : Doctor, I see Spots or clouds in my vision. I can't see anything clearly. I feel helpless.",
   'Doctor : I understand how you feel. I need to ask a few questions to diagnose your disease. Have you got Diminished vision?',
   'Patient : True, I am also dealing with Diminished vision.',
   'Doctor : Do you have Symptoms of eye?',
   'Patient : Yes, I have got Symptoms of eye.',
   'Doctor : Have you felt Pain in eye?',
   'Patient : Indeed, I am suffering from Pain in eye.',
   'Doctor : Your symptoms indicate that you have [MASK].'],
  'disease_tag': 'central retinal artery or vein occlusion'},
 {'dialog_id': 19510,
  'masked_dialog': ['Patient : Doctor, I have Shoulder pain. I feel terrible. Would you please tell me what could be its cause?',
   'Doctor :  I can feel the pain you feel. Let me ask you some questions. Do you have Back pain?',
   'Patient : Literally, I am suffering from Back pain.',
   'Doctor : Do you have Low back pa

In [25]:
len(all_dialog_file)

1396

In [26]:
with open("all_dialog_file.p", "wb") as f:
    pickle.dump(all_dialog_file, f)

In [27]:
with open("all_dialog_file.p", "rb") as f:
    temp_all = pickle.load(f)

In [29]:
temp_all

[{'dialog_id': 1059,
  'masked_dialog': ["Patient : Doctor, I see Spots or clouds in my vision. I can't see anything clearly. I feel helpless.",
   'Doctor : I understand how you feel. I need to ask a few questions to diagnose your disease. Have you got Diminished vision?',
   'Patient : True, I am also dealing with Diminished vision.',
   'Doctor : Do you have Symptoms of eye?',
   'Patient : Yes, I have got Symptoms of eye.',
   'Doctor : Have you felt Pain in eye?',
   'Patient : Indeed, I am suffering from Pain in eye.',
   'Doctor : Your symptoms indicate that you have [MASK].'],
  'disease_tag': 'central retinal artery or vein occlusion'},
 {'dialog_id': 19510,
  'masked_dialog': ['Patient : Doctor, I have Shoulder pain. I feel terrible. Would you please tell me what could be its cause?',
   'Doctor :  I can feel the pain you feel. Let me ask you some questions. Do you have Back pain?',
   'Patient : Literally, I am suffering from Back pain.',
   'Doctor : Do you have Low back pa

In [30]:
len(temp_all)

1396

In [31]:
all_self_report_file = []

for i in range(len(all_dialog_file)):
    dlog = all_dialog_file[i]['masked_dialog']
    dlog_id = all_dialog_file[i]['dialog_id']
    disease = all_dialog_file[i]['disease_tag']
    
    first_utterance = dlog[0]
    
    temp_dict = {}
    
    temp_dict['dialog_id'] = dlog_id
    temp_dict['first_utterance'] = first_utterance
    temp_dict['disease_tag'] = disease
    
    all_self_report_file.append(temp_dict)

In [32]:
all_self_report_file[970]

{'dialog_id': 739,
 'first_utterance': 'Patient : Doctor, I am having trouble with Diminished hearing. I am avoiding socila setting because of it.',
 'disease_tag': 'epidural hemorrhage'}

In [33]:
all_dialog_file[970]

{'dialog_id': 739,
 'masked_dialog': ['Patient : Doctor, I am having trouble with Diminished hearing. I am avoiding socila setting because of it.',
  "Doctor : That must have made you feel lonely. I'm here for you. Can you say, do you have any Depressive or psychotic symptoms?",
  'Patient : I do have Doctor. It is making me lose interest in everything.',
  'Doctor : I understand what you are feeling. Are you suffering from Side pain too?',
  'Patient : Yes, I am suffering from Side pain.',
  'Doctor : You might have [MASK]'],
 'disease_tag': 'epidural hemorrhage'}

In [34]:
with open("all_self_report_file.p", "wb") as f:
    pickle.dump(all_self_report_file, f)

In [35]:
with open("all_self_report_file.p", "rb") as f:
    temp_self = pickle.load(f)

In [36]:
temp_self[1234]

{'dialog_id': 28980,
 'first_utterance': 'Patient : Hello Doctor, why do I have leg pain? It would be great to be free of this as soon as possible.',
 'disease_tag': 'ganglion cyst'}

In [37]:
all_self_report_file[1234]

{'dialog_id': 28980,
 'first_utterance': 'Patient : Hello Doctor, why do I have leg pain? It would be great to be free of this as soon as possible.',
 'disease_tag': 'ganglion cyst'}

In [38]:
with open("DID.p", "rb") as f:
    did = pickle.load(f)

In [39]:
print(len(did))
did

90


{'Acanthosis nigricans': 'D_3',
 'Acariasis': 'D_85',
 'Acne': 'D_53',
 'Actinic keratosis': 'D_12',
 'Acute glaucoma': 'D_48',
 'Acute kidney injury': 'D_86',
 'Acute stress reaction': 'D_76',
 'Adhesive capsulitis of the shoulder': 'D_42',
 'Adjustment reaction': 'D_33',
 'Air embolism': 'D_78',
 'Alcohol intoxication': 'D_47',
 'Allergy': 'D_28',
 'Alzheimer disease': 'D_79',
 'Amyloidosis': 'D_59',
 'Amyotrophic lateral sclerosis ALS': 'D_4',
 'Ankylosing spondylitis': 'D_75',
 'Anxiety': 'D_82',
 'Aphakia': 'D_50',
 'Carbon monoxide poisoning': 'D_38',
 'Carcinoid syndrome': 'D_44',
 'Carpal tunnel syndrome': 'D_64',
 'Cat scratch disease': 'D_58',
 'Central retinal artery or vein occlusion': 'D_80',
 'Cerebral edema': 'D_51',
 'Chagas disease': 'D_61',
 'Chalazion': 'D_37',
 'Chancroid': 'D_74',
 'Chickenpox': 'D_27',
 'Chlamydia': 'D_23',
 'Chondromalacia of the patella': 'D_84',
 'Chronic back pain': 'D_19',
 'Chronic kidney disease': 'D_7',
 'Chronic pain disorder': 'D_56',
 '

In [40]:
with open("SID.p", "rb") as f:
    sid = pickle.load(f)

In [41]:
print(len(sid))
sid

266


{'Abnormal appearing skin': 'S_237',
 'Abnormal involuntary movements': 'S_141',
 'Abnormal movement of eyelid': 'S_180',
 'Abnormal size or shape of ear': 'S_242',
 'Absence of menstruation': 'S_99',
 'Abusing alcohol': 'S_41',
 'Ache all over': 'S_88',
 'Acne or pimples': 'S_29',
 'Allergic reaction': 'S_169',
 'Ankle pain': 'S_131',
 'Ankle stiffness or tightness': 'S_87',
 'Ankle swelling': 'S_76',
 'Anxiety and nervousness': 'S_10',
 'Apnea': 'S_53',
 'Arm lump or mass': 'S_199',
 'Arm pain': 'S_77',
 'Arm stiffness or tightness': 'S_250',
 'Arm swelling': 'S_245',
 'Arm weakness': 'S_3',
 'Back cramps or spasms': 'S_35',
 'Back mass or lump': 'S_189',
 'Back pain': 'S_73',
 'Back stiffness or tightness': 'S_142',
 'Back weakness': 'S_94',
 'Bladder mass': 'S_123',
 'Bleeding from eye': 'S_235',
 'Bleeding gums': 'S_216',
 'Bleeding or discharge from nipple': 'S_46',
 'Blindness': 'S_262',
 'Blood in urine': 'S_254',
 'Bones are painful': 'S_158',
 'Bowlegged or knock-kneed': 'S_2

In [42]:
sid_small = {}
for i in sid:
    key = i.lower()
    print(key)
    
    sid_small[key] = sid[i]
    print(sid_small[key])
    print()

abnormal appearing skin
S_237

abnormal involuntary movements
S_141

abnormal movement of eyelid
S_180

abnormal size or shape of ear
S_242

absence of menstruation
S_99

abusing alcohol
S_41

ache all over
S_88

acne or pimples
S_29

allergic reaction
S_169

ankle pain
S_131

ankle stiffness or tightness
S_87

ankle swelling
S_76

anxiety and nervousness
S_10

apnea
S_53

arm lump or mass
S_199

arm pain
S_77

arm stiffness or tightness
S_250

arm swelling
S_245

arm weakness
S_3

back cramps or spasms
S_35

back mass or lump
S_189

back pain
S_73

back stiffness or tightness
S_142

back weakness
S_94

bladder mass
S_123

bleeding from eye
S_235

bleeding gums
S_216

bleeding or discharge from nipple
S_46

blindness
S_262

blood in urine
S_254

bones are painful
S_158

bowlegged or knock-kneed
S_257

burning abdominal pain
S_232

chest tightness
S_58

chills
S_172

congestion in chest
S_226

coryza
S_156

cough
S_0

cramps and spasms
S_212

cross-eyed
S_97

decreased appetite
S_264

d

In [43]:
sid_small

{'abnormal appearing skin': 'S_237',
 'abnormal involuntary movements': 'S_141',
 'abnormal movement of eyelid': 'S_180',
 'abnormal size or shape of ear': 'S_242',
 'absence of menstruation': 'S_99',
 'abusing alcohol': 'S_41',
 'ache all over': 'S_88',
 'acne or pimples': 'S_29',
 'allergic reaction': 'S_169',
 'ankle pain': 'S_131',
 'ankle stiffness or tightness': 'S_87',
 'ankle swelling': 'S_76',
 'anxiety and nervousness': 'S_10',
 'apnea': 'S_53',
 'arm lump or mass': 'S_199',
 'arm pain': 'S_77',
 'arm stiffness or tightness': 'S_250',
 'arm swelling': 'S_245',
 'arm weakness': 'S_3',
 'back cramps or spasms': 'S_35',
 'back mass or lump': 'S_189',
 'back pain': 'S_73',
 'back stiffness or tightness': 'S_142',
 'back weakness': 'S_94',
 'bladder mass': 'S_123',
 'bleeding from eye': 'S_235',
 'bleeding gums': 'S_216',
 'bleeding or discharge from nipple': 'S_46',
 'blindness': 'S_262',
 'blood in urine': 'S_254',
 'bones are painful': 'S_158',
 'bowlegged or knock-kneed': 'S_2

In [55]:
with open("/Users/mohit/Documents/Machine Learning/Practice/27/symptom_extraction/input_utterance/sample_pred_out2.txt") as f:
    lines_output = f.readlines()

In [56]:
lines_output

['<Symptom> -> Dialog id : 1059\n',
 "<Symptom> -> Patient : Doctor, I see [Spots:B-Symptom] [or:I-Symptom] [clouds:I-Symptom] [in:I-Symptom] my [vision.:I-Symptom] I can't see anything [clearly.:I-Symptom] I feel [helpless.:B-Symptom]\n",
 '<Symptom> -> Doctor : I understand how you feel. I need to ask a few questions to diagnose your disease. Have you got [Diminished:B-Symptom] [vision?:I-Symptom]\n',
 '<Symptom> -> Patient : True, I am also dealing with [Diminished:B-Symptom] [vision.:I-Symptom]\n',
 '<Symptom> -> Doctor : Do you have [Symptoms:B-Symptom] [of:I-Symptom] [eye?:I-Symptom]\n',
 '<Symptom> -> Patient : Yes, I have got [Symptoms:B-Symptom] [of:I-Symptom] [eye.:I-Symptom]\n',
 '<Symptom> -> Doctor : Have you felt [Pain:B-Symptom] [in:I-Symptom] [eye?:I-Symptom]\n',
 '<Symptom> -> Patient : Indeed, I am suffering from [Pain:B-Symptom] [in:I-Symptom] [eye.:I-Symptom]\n',
 '<Symptom> -> Doctor : Your symptoms indicate that you have [MASK].\n',
 '<Symptom> -> Dialog id : 1951

In [57]:
len(lines_output)

10587

In [59]:
type(lines_output)

list

In [60]:
lines_output[-10:]

['<Symptom> -> Dialog id : 28944\n',
 "<Symptom> -> Patient : I've been experiencing [abnormal:B-Symptom] [involuntary:I-Symptom] [movements.:I-Symptom] It is causing [sudden:B-Symptom] [jerking:I-Symptom] [of:I-Symptom] my [arm:I-Symptom] [muscles,:I-Symptom] please help.\n",
 '<Symptom> -> Doctor : I can understand how hard it is to control [sudden:B-Symptom] [jerking.:I-Symptom] It may be due to [MASK].\n',
 '<Symptom> -> Dialog id : 1563\n',
 "<Symptom> -> Patient : Doctor, I'm suffering from [palpitations.:B-Symptom] Sometimes my [heart:B-Symptom] [beat:I-Symptom] [irregularly,:B-Symptom] please help.\n",
 '<Symptom> -> Doctor : I am here so that you move out of this condition. Do you have [anxiety:B-Symptom] [and:I-Symptom] [nervousness?:I-Symptom]\n',
 '<Affirmative> -> Patient : Yes.\n',
 '<Symptom> -> Doctor : Do you suffer from [insomnia?:B-Symptom]\n',
 '<Symptom> -> Patient : Yes, I have [insomnia.:B-Symptom]\n',
 '<Symptom> -> Doctor : You are suffering from [MASK].\n']

In [52]:
with open("/Users/mohit/Documents/Machine Learning/Practice/27/symptom_extraction/input_utterance/sample_pred_in2.txt") as f:
    lines_input = f.readlines()

In [53]:
lines_input

['Dialog id : 1059\n',
 "Patient : Doctor, I see Spots or clouds in my vision. I can't see anything clearly. I feel helpless.\n",
 'Doctor : I understand how you feel. I need to ask a few questions to diagnose your disease. Have you got Diminished vision?\n',
 'Patient : True, I am also dealing with Diminished vision.\n',
 'Doctor : Do you have Symptoms of eye?\n',
 'Patient : Yes, I have got Symptoms of eye.\n',
 'Doctor : Have you felt Pain in eye?\n',
 'Patient : Indeed, I am suffering from Pain in eye.\n',
 'Doctor : Your symptoms indicate that you have [MASK].\n',
 'Dialog id : 19510\n',
 'Patient : Doctor, I have Shoulder pain. I feel terrible. Would you please tell me what could be its cause?\n',
 'Doctor :  I can feel the pain you feel. Let me ask you some questions. Do you have Back pain?\n',
 'Patient : Literally, I am suffering from Back pain.\n',
 'Doctor : Do you have Low back pain?\n',
 'Patient : Yes, I am dealing with Low back pain.\n',
 'Doctor : Are you also dealing w

In [54]:
len(lines_input)

10587

In [61]:
lines_output[:10]

['<Symptom> -> Dialog id : 1059\n',
 "<Symptom> -> Patient : Doctor, I see [Spots:B-Symptom] [or:I-Symptom] [clouds:I-Symptom] [in:I-Symptom] my [vision.:I-Symptom] I can't see anything [clearly.:I-Symptom] I feel [helpless.:B-Symptom]\n",
 '<Symptom> -> Doctor : I understand how you feel. I need to ask a few questions to diagnose your disease. Have you got [Diminished:B-Symptom] [vision?:I-Symptom]\n',
 '<Symptom> -> Patient : True, I am also dealing with [Diminished:B-Symptom] [vision.:I-Symptom]\n',
 '<Symptom> -> Doctor : Do you have [Symptoms:B-Symptom] [of:I-Symptom] [eye?:I-Symptom]\n',
 '<Symptom> -> Patient : Yes, I have got [Symptoms:B-Symptom] [of:I-Symptom] [eye.:I-Symptom]\n',
 '<Symptom> -> Doctor : Have you felt [Pain:B-Symptom] [in:I-Symptom] [eye?:I-Symptom]\n',
 '<Symptom> -> Patient : Indeed, I am suffering from [Pain:B-Symptom] [in:I-Symptom] [eye.:I-Symptom]\n',
 '<Symptom> -> Doctor : Your symptoms indicate that you have [MASK].\n',
 '<Symptom> -> Dialog id : 1951

In [103]:
len(lines_output)

10587

In [115]:
d_number = []

all_dlog_id = []

temp_line_id_list = []

for i in range(len(lines_input)):
    temp_line = lines_input[i]
    
    
    present = re.search("Dialog id", temp_line)
    
    
    if present:
        d_number.append(i)
        idx = temp_line.index(":")
        print(temp_line)
        print(idx)
        print(temp_line[idx:])
        print(temp_line[:idx])
        print(len(temp_line[idx]))
        idx2 = temp_line.index("\n")
        print("New line index : ", idx2)
        print("Length of temp line : ", len(temp_line))
        print("ID extracted : ", int(temp_line[idx+2:idx2]))
        print("ID extracted type : ", type(int(temp_line[idx+2:idx2])))
        temp_dict = {}
        
        temp_dict['dialog_line'] = i
        temp_dict['dialog_id'] = int(temp_line[idx+2:idx2])
        
        temp_line_id_list.append(temp_dict)
        
        print()
        
#     else:
        
    

Dialog id : 1059

10
: 1059

Dialog id 
1
New line index :  16
Length of temp line :  17
ID extracted :  1059
ID extracted type :  <class 'int'>

Dialog id : 19510

10
: 19510

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  19510
ID extracted type :  <class 'int'>

Dialog id : 25630

10
: 25630

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  25630
ID extracted type :  <class 'int'>

Dialog id : 1467

10
: 1467

Dialog id 
1
New line index :  16
Length of temp line :  17
ID extracted :  1467
ID extracted type :  <class 'int'>

Dialog id : 5780

10
: 5780

Dialog id 
1
New line index :  16
Length of temp line :  17
ID extracted :  5780
ID extracted type :  <class 'int'>

Dialog id : 26258

10
: 26258

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  26258
ID extracted type :  <class 'int'>

Dialog id : 22733

10
: 22733

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  22733
ID

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  25428
ID extracted type :  <class 'int'>

Dialog id : 8663

10
: 8663

Dialog id 
1
New line index :  16
Length of temp line :  17
ID extracted :  8663
ID extracted type :  <class 'int'>

Dialog id : 4031

10
: 4031

Dialog id 
1
New line index :  16
Length of temp line :  17
ID extracted :  4031
ID extracted type :  <class 'int'>

Dialog id : 14652

10
: 14652

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  14652
ID extracted type :  <class 'int'>

Dialog id : 8617

10
: 8617

Dialog id 
1
New line index :  16
Length of temp line :  17
ID extracted :  8617
ID extracted type :  <class 'int'>

Dialog id : 12841

10
: 12841

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  12841
ID extracted type :  <class 'int'>

Dialog id : 14819

10
: 14819

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  14819
ID extracted type :  <class 'int'

New line index :  17
Length of temp line :  18
ID extracted :  16180
ID extracted type :  <class 'int'>

Dialog id : 2579

10
: 2579

Dialog id 
1
New line index :  16
Length of temp line :  17
ID extracted :  2579
ID extracted type :  <class 'int'>

Dialog id : 11238

10
: 11238

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  11238
ID extracted type :  <class 'int'>

Dialog id : 10789

10
: 10789

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  10789
ID extracted type :  <class 'int'>

Dialog id : 9566

10
: 9566

Dialog id 
1
New line index :  16
Length of temp line :  17
ID extracted :  9566
ID extracted type :  <class 'int'>

Dialog id : 22709

10
: 22709

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  22709
ID extracted type :  <class 'int'>

Dialog id : 1557

10
: 1557

Dialog id 
1
New line index :  16
Length of temp line :  17
ID extracted :  1557
ID extracted type :  <class 'int'>

Dialog id 

Length of temp line :  18
ID extracted :  17183
ID extracted type :  <class 'int'>

Dialog id : 29099

10
: 29099

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  29099
ID extracted type :  <class 'int'>

Dialog id : 443

10
: 443

Dialog id 
1
New line index :  15
Length of temp line :  16
ID extracted :  443
ID extracted type :  <class 'int'>

Dialog id : 14387

10
: 14387

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  14387
ID extracted type :  <class 'int'>

Dialog id : 7252

10
: 7252

Dialog id 
1
New line index :  16
Length of temp line :  17
ID extracted :  7252
ID extracted type :  <class 'int'>

Dialog id : 24514

10
: 24514

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  24514
ID extracted type :  <class 'int'>

Dialog id : 22913

10
: 22913

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  22913
ID extracted type :  <class 'int'>

Dialog id : 26877

10
: 26877



ID extracted :  22065
ID extracted type :  <class 'int'>

Dialog id : 16394

10
: 16394

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  16394
ID extracted type :  <class 'int'>

Dialog id : 949

10
: 949

Dialog id 
1
New line index :  15
Length of temp line :  16
ID extracted :  949
ID extracted type :  <class 'int'>

Dialog id : 27291

10
: 27291

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  27291
ID extracted type :  <class 'int'>

Dialog id : 26762

10
: 26762

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  26762
ID extracted type :  <class 'int'>

Dialog id : 22795

10
: 22795

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  22795
ID extracted type :  <class 'int'>

Dialog id : 562

10
: 562

Dialog id 
1
New line index :  15
Length of temp line :  16
ID extracted :  562
ID extracted type :  <class 'int'>

Dialog id : 9366

10
: 9366

Dialog id 
1
New line index :  

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  21028
ID extracted type :  <class 'int'>

Dialog id : 22412

10
: 22412

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  22412
ID extracted type :  <class 'int'>

Dialog id : 5880

10
: 5880

Dialog id 
1
New line index :  16
Length of temp line :  17
ID extracted :  5880
ID extracted type :  <class 'int'>

Dialog id : 4163

10
: 4163

Dialog id 
1
New line index :  16
Length of temp line :  17
ID extracted :  4163
ID extracted type :  <class 'int'>

Dialog id : 2504

10
: 2504

Dialog id 
1
New line index :  16
Length of temp line :  17
ID extracted :  2504
ID extracted type :  <class 'int'>

Dialog id : 25173

10
: 25173

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  25173
ID extracted type :  <class 'int'>

Dialog id : 17912

10
: 17912

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  17912
ID extracted type :  <class 'int'

Length of temp line :  18
ID extracted :  12173
ID extracted type :  <class 'int'>

Dialog id : 4033

10
: 4033

Dialog id 
1
New line index :  16
Length of temp line :  17
ID extracted :  4033
ID extracted type :  <class 'int'>

Dialog id : 7260

10
: 7260

Dialog id 
1
New line index :  16
Length of temp line :  17
ID extracted :  7260
ID extracted type :  <class 'int'>

Dialog id : 20452

10
: 20452

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  20452
ID extracted type :  <class 'int'>

Dialog id : 3225

10
: 3225

Dialog id 
1
New line index :  16
Length of temp line :  17
ID extracted :  3225
ID extracted type :  <class 'int'>

Dialog id : 2096

10
: 2096

Dialog id 
1
New line index :  16
Length of temp line :  17
ID extracted :  2096
ID extracted type :  <class 'int'>

Dialog id : 15503

10
: 15503

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  15503
ID extracted type :  <class 'int'>

Dialog id : 27214

10
: 27214

Dia


Dialog id 
1
New line index :  16
Length of temp line :  17
ID extracted :  2270
ID extracted type :  <class 'int'>

Dialog id : 9952

10
: 9952

Dialog id 
1
New line index :  16
Length of temp line :  17
ID extracted :  9952
ID extracted type :  <class 'int'>

Dialog id : 13788

10
: 13788

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  13788
ID extracted type :  <class 'int'>

Dialog id : 16448

10
: 16448

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  16448
ID extracted type :  <class 'int'>

Dialog id : 27719

10
: 27719

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  27719
ID extracted type :  <class 'int'>

Dialog id : 6981

10
: 6981

Dialog id 
1
New line index :  16
Length of temp line :  17
ID extracted :  6981
ID extracted type :  <class 'int'>

Dialog id : 21808

10
: 21808

Dialog id 
1
New line index :  17
Length of temp line :  18
ID extracted :  21808
ID extracted type :  <class 'i

In [116]:
temp_line

'Doctor : You are suffering from [MASK].\n'

In [117]:
temp_line_id_list

[{'dialog_line': 0, 'dialog_id': 1059},
 {'dialog_line': 9, 'dialog_id': 19510},
 {'dialog_line': 22, 'dialog_id': 25630},
 {'dialog_line': 25, 'dialog_id': 1467},
 {'dialog_line': 32, 'dialog_id': 5780},
 {'dialog_line': 53, 'dialog_id': 26258},
 {'dialog_line': 59, 'dialog_id': 22733},
 {'dialog_line': 70, 'dialog_id': 1564},
 {'dialog_line': 77, 'dialog_id': 29211},
 {'dialog_line': 88, 'dialog_id': 26235},
 {'dialog_line': 95, 'dialog_id': 16427},
 {'dialog_line': 105, 'dialog_id': 16512},
 {'dialog_line': 116, 'dialog_id': 17308},
 {'dialog_line': 139, 'dialog_id': 16360},
 {'dialog_line': 146, 'dialog_id': 15081},
 {'dialog_line': 153, 'dialog_id': 15386},
 {'dialog_line': 166, 'dialog_id': 18363},
 {'dialog_line': 173, 'dialog_id': 27441},
 {'dialog_line': 178, 'dialog_id': 9641},
 {'dialog_line': 183, 'dialog_id': 27768},
 {'dialog_line': 197, 'dialog_id': 21778},
 {'dialog_line': 201, 'dialog_id': 18706},
 {'dialog_line': 210, 'dialog_id': 7857},
 {'dialog_line': 215, 'dialog_

In [118]:
len(temp_line_id_list)

1396

In [119]:
len(d_number)

1396

In [121]:
d_number[:10]

[0, 9, 22, 25, 32, 53, 59, 70, 77, 88]

In [129]:
dialog_bio_list = []
for i in range(len(temp_line_id_list)):
    if(i == len(temp_line_id_list) - 1):
        first = temp_line_id_list[i]['dialog_line']
        curr_dialog_id = temp_line_id_list[i]['dialog_id']
#         second = temp_line_id_list[i+1]['dialog_line']

        temp_list = []
        temp_dict = {}

        for j in range(first+1, len(lines_output)):
            temp_line = lines_output[j]
            print(temp_line)
            temp_list.append(temp_line)

        print()

        temp_dict['dialog_id'] = curr_dialog_id
        temp_dict["symptom_tag"] = temp_list
        dialog_bio_list.append(temp_dict)
    
    else:
        first = temp_line_id_list[i]['dialog_line']
        curr_dialog_id = temp_line_id_list[i]['dialog_id']
        second = temp_line_id_list[i+1]['dialog_line']

        temp_list = []
        temp_dict = {}

        for j in range(first+1, second):
            temp_line = lines_output[j]
            print(temp_line)
            temp_list.append(temp_line)

        print()

        temp_dict['dialog_id'] = curr_dialog_id
        temp_dict["symptom_tag"] = temp_list
        dialog_bio_list.append(temp_dict)
        
    
    
    
    
    

<Symptom> -> Patient : Doctor, I see [Spots:B-Symptom] [or:I-Symptom] [clouds:I-Symptom] [in:I-Symptom] my [vision.:I-Symptom] I can't see anything [clearly.:I-Symptom] I feel [helpless.:B-Symptom]

<Symptom> -> Doctor : I understand how you feel. I need to ask a few questions to diagnose your disease. Have you got [Diminished:B-Symptom] [vision?:I-Symptom]

<Symptom> -> Patient : True, I am also dealing with [Diminished:B-Symptom] [vision.:I-Symptom]

<Symptom> -> Doctor : Do you have [Symptoms:B-Symptom] [of:I-Symptom] [eye?:I-Symptom]

<Symptom> -> Patient : Yes, I have got [Symptoms:B-Symptom] [of:I-Symptom] [eye.:I-Symptom]

<Symptom> -> Doctor : Have you felt [Pain:B-Symptom] [in:I-Symptom] [eye?:I-Symptom]

<Symptom> -> Patient : Indeed, I am suffering from [Pain:B-Symptom] [in:I-Symptom] [eye.:I-Symptom]

<Symptom> -> Doctor : Your symptoms indicate that you have [MASK].


<Symptom> -> Patient : Doctor, I have [Shoulder:B-Symptom] [pain.:I-Symptom] I feel terrible. Would you pl


<Affirmative> -> Patient : That is right, doctor.

<Symptom> -> Doctor : Are you suffering from [Depressive:B-Symptom] [or:I-Symptom] [psychotic:I-Symptom] [symptoms?:I-Symptom]

<Affirmative> -> Patient : Absolutely, I am struggling with them.

<Symptom> -> Doctor : Have you felt [Depression?:B-Symptom]

<Symptom> -> Patient : Yes, I am going through [Depression:B-Symptom] too.

<Symptom> -> Doctor : Do you have [Sharp:B-Symptom] [chest:I-Symptom] [pain?:I-Symptom]

<Symptom> -> Patient : True, I have got [Sharp:B-Symptom] [chest:I-Symptom] [pain.:I-Symptom]

<Symptom> -> Doctor : OK, I think you have [MASK].


<Symptom> -> Patient : Doctor, I am suffering from [Hand:B-Symptom] [or:I-Symptom] [finger:I-Symptom] [pain.:I-Symptom] I am unable to study or work on my laptop.

<Symptom> -> Doctor : OK, are you also dealing with [Knee:B-Symptom] [pain?:I-Symptom]

<Symptom> -> Patient : Indeed, I have got [Knee:B-Symptom] [pain.:I-Symptom]

<Symptom> -> Doctor : Do you have [Leg:B-Symptom]

<Affirmative> -> Patient : True, doctor.

<Symptom> -> Doctor : OK, you may have [MASK].


<Symptom> -> Patient : Hi doctor, I have got [Skin:B-Symptom] [lesion.:I-Symptom] Please, let me know its cause. I am unable to [eat:I-Symptom] [anything.:I-Symptom]

<Affirmative> -> Doctor : I totally get it. I think you have got [MASK].


<Symptom> -> Patient : Hello doctor, I am suffering from [Lack:B-Symptom] [of:I-Symptom] [growth.:I-Symptom] I want to play different games but I cannot because of this.

<Symptom> -> Doctor : I totally get it. You must feel so helpless. Do you have [Diminished:B-Symptom] [hearing?:I-Symptom]

<Affirmative> -> Patient : You are right.

<Symptom> -> Doctor : Have you got [Ear:B-Symptom] [pain?:I-Symptom]

<Symptom> -> Patient : Yes, I have got [Ear:B-Symptom] [pain.:I-Symptom]

<Affirmative> -> Doctor : Then, you might have [MASK].


<Symptom> -> Patient : Doctor, I am going through [Excessive:B-Symptom] [anger.:I-Symptom] I am willing to get rid of this as so


<Symptom> -> Patient : Doctor, I have got [Pain:B-Symptom] [during:I-Symptom] [pregnanacy.:I-Symptom]

<Symptom> -> Doctor : Let me know do you have [Pain:B-Symptom] [in:I-Symptom] [eye?:I-Symptom]

<Affirmative> -> Patient : Yes Doctor.

<Symptom> -> Doctor : Have you got [Facial:B-Symptom] [pain?:I-Symptom]

<Symptom> -> Patient : Right, I have [Facial:B-Symptom] [pain.:I-Symptom]

<Symptom> -> Doctor : Are you also suffering from [Ankle:B-Symptom] [pain?:I-Symptom]

<Affirmative> -> Patient : Yes Doctor.

<Symptom> -> Doctor : Do you have [Wrist:B-Symptom] [pain?:I-Symptom]

<Symptom> -> Patient : True, I am suffering from [Wrist:B-Symptom] [pain.:I-Symptom]

<Symptom> -> Doctor : Are you dealing with [Excessive:B-Symptom] [anger?:I-Symptom]

<Affirmative> -> Patient : Yes Doctor, I am dealing with it.

<Symptom> -> Doctor : Have you felt [Joint:B-Symptom] [stiffness:I-Symptom] [or:I-Symptom] [tightness?:I-Symptom]

<Affirmative> -> Patient : Yes.

<Symptom> -> Doctor : Are you als


<Symptom> -> Patient : Why am I struggling with [fatigue?:B-Symptom] I have heard that [fatigue:B-Symptom] may be the symptom of several serious [diseases.:I-Symptom] That's why I am bothered also.

<Symptom> -> Doctor : You are true. One relevant question-are you also experiencing [shortness:B-Symptom] [of:I-Symptom] [breath?:I-Symptom]

<Affirmative> -> Patient : Yes, sometimes.

<Symptom> -> Doctor : This may be due to [MASK].


<Symptom> -> Patient : I am struggling with [depressive:B-Symptom] [or:I-Symptom] [psychotic:I-Symptom] [symptoms.:I-Symptom] I can't follow why I am feeling so. I am having such symptoms for the last three months. But why it is happening?

<Symptom> -> Doctor : No need to think of. Are you noticing [decreased:B-Symptom] [appetite?:I-Symptom]

<Affirmative> -> Patient : Yes.

<Symptom> -> Doctor : Have you support from [weight:B-Symptom] [gain:I-Symptom] recently?

<Affirmative> -> Patient : Yes I have.

<Symptom> -> Doctor : It seems that you may have an [

In [130]:
dialog_bio_list

[{'dialog_id': 1059,
  'symptom_tag': ["<Symptom> -> Patient : Doctor, I see [Spots:B-Symptom] [or:I-Symptom] [clouds:I-Symptom] [in:I-Symptom] my [vision.:I-Symptom] I can't see anything [clearly.:I-Symptom] I feel [helpless.:B-Symptom]\n",
   '<Symptom> -> Doctor : I understand how you feel. I need to ask a few questions to diagnose your disease. Have you got [Diminished:B-Symptom] [vision?:I-Symptom]\n',
   '<Symptom> -> Patient : True, I am also dealing with [Diminished:B-Symptom] [vision.:I-Symptom]\n',
   '<Symptom> -> Doctor : Do you have [Symptoms:B-Symptom] [of:I-Symptom] [eye?:I-Symptom]\n',
   '<Symptom> -> Patient : Yes, I have got [Symptoms:B-Symptom] [of:I-Symptom] [eye.:I-Symptom]\n',
   '<Symptom> -> Doctor : Have you felt [Pain:B-Symptom] [in:I-Symptom] [eye?:I-Symptom]\n',
   '<Symptom> -> Patient : Indeed, I am suffering from [Pain:B-Symptom] [in:I-Symptom] [eye.:I-Symptom]\n',
   '<Symptom> -> Doctor : Your symptoms indicate that you have [MASK].\n']},
 {'dialog_id'

In [131]:
len(dialog_bio_list)

1396

In [133]:
dialog_bio_list[-3:]

[{'dialog_id': 11613,
  'symptom_tag': ['<Symptom> -> Patient : I have [knee:B-Symptom] [pain.:I-Symptom]\n',
   '<Symptom> -> Doctor : Do you have [foot:B-Symptom] [or:I-Symptom] [toe:I-Symptom] [pain?:I-Symptom]\n',
   '<Affirmative> -> Patient : Yes.\n',
   '<Symptom> -> Doctor : Do you have [foot:B-Symptom] [or:I-Symptom] [toe:I-Symptom] [swelling?:I-Symptom]\n',
   '<Symptom> -> Patient : I am not quite certain [Foot:B-Symptom] [or:I-Symptom] [toe:I-Symptom] [swelling.:I-Symptom]\n',
   '<Symptom> -> Doctor : Do you have [wrist:B-Symptom] [pain?:I-Symptom]\n',
   '<Affirmative> -> Patient : Yeah, I do.\n',
   '<Symptom> -> Doctor : You are suffering from [MASK].\n']},
 {'dialog_id': 28944,
  'symptom_tag': ["<Symptom> -> Patient : I've been experiencing [abnormal:B-Symptom] [involuntary:I-Symptom] [movements.:I-Symptom] It is causing [sudden:B-Symptom] [jerking:I-Symptom] [of:I-Symptom] my [arm:I-Symptom] [muscles,:I-Symptom] please help.\n",
   '<Symptom> -> Doctor : I can unders

In [128]:
temp_line_id_list[-3:]

[{'dialog_line': 10568, 'dialog_id': 11613},
 {'dialog_line': 10577, 'dialog_id': 28944},
 {'dialog_line': 10580, 'dialog_id': 1563}]